<a href="https://colab.research.google.com/github/tanish495/Dynamic-Pricing-for-Urban-Parking-Lots/blob/main/capstoneproject.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

***Installing functions/libraries***

In [10]:
!pip install bokeh
!pip install bokeh geopy --quiet

***Importing all the variables***

In [11]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import datetime
from datetime import datetime
import bokeh.plotting
from bokeh.plotting import figure, output_notebook, show
from bokeh.models import ColumnDataSource, HoverTool
from bokeh.layouts import column
output_notebook()
import panel as pn
from geopy.distance import geodesic

***Adding Dataset***

In [8]:
df = pd.read_csv("/content/dataset.csv")
df.head()

ID SystemCodeNumber  Capacity   Latitude  Longitude  Occupancy VehicleType  \
0   0      BHMBCCMKT01       577  26.144536  91.736172       61.0         car   
1   1      BHMBCCMKT01       577  26.144536  91.736172       64.0         car   
2   2      BHMBCCMKT01       577  26.144536  91.736172       80.0         car   
3   3      BHMBCCMKT01       577  26.144536  91.736172      107.0         car   
4   4      BHMBCCMKT01       577  26.144536  91.736172      150.0        bike   

  TrafficConditionNearby  QueueLength  IsSpecialDay LastUpdatedDate  \
0                    low          1.0           0.0      04-10-2016   
1                    low          1.0           0.0      04-10-2016   
2                    low          2.0           0.0      04-10-2016   
3                    low          2.0           0.0      04-10-2016   
4                    low          2.0           0.0      04-10-2016   

  LastUpdatedTime  
0        07:59:00  
1        08:25:00  
2        08:59:00  
3        09:32:00  
4        09:59:00

***MODEL 1 :-*** Baseline Linear Model

In [9]:
# Step 1: Combining the data and time into one
df['Datetime'] = pd.to_datetime(df['LastUpdatedDate'] + ' ' + df['LastUpdatedTime'], format="%d-%m-%Y %H:%M:%S")
df = df.sort_values(by='Datetime')

# Step 2: Define Baseline Pricing Model
def baseline_linear_pricing(df, alpha=10, initial_price=50):
    prices = [initial_price]
    for i in range(1, len(df)):
        prev_price = prices[-1]
        occ = df.iloc[i]['Occupancy']
        cap = df.iloc[i]['Capacity']
        occupancy_ratio = occ / cap
        new_price = prev_price + alpha * occupancy_ratio
        prices.append(new_price)
    df['PredictedPrice'] = prices
    return df

# Step 3: Run the model
df = baseline_linear_pricing(df, alpha=10, initial_price=50)

# Step 4: Prepare Bokeh Plot
source = ColumnDataSource(df)

p = figure(x_axis_type='datetime', title="Baseline Linear Dynamic Pricing", width=800, height=400)
p.line(x='Datetime', y='PredictedPrice', source=source, legend_label='Predicted Price', line_width=2, color='navy')
p.circle(x='Datetime', y='PredictedPrice', source=source, size=8, color='orange', legend_label='Data Point')

# Add hover tool
hover = HoverTool(tooltips=[
    ("Time", "@Datetime{%F %T}"),
    ("Price", "@PredictedPrice{0.00}"),
    ("Occupancy", "@Occupancy"),
    ("Capacity", "@Capacity")
], formatters={'@Datetime': 'datetime'})

p.add_tools(hover)
p.xaxis.axis_label = 'Time'
p.yaxis.axis_label = 'Price'
p.legend.location = 'top_left'

# Step 5: Show plot
show(p)

# Optional: Display final data
df[['Datetime', 'Occupancy', 'Capacity', 'PredictedPrice']]


Datetime  Occupancy  Capacity  PredictedPrice
0     2016-10-04 07:59:00       61.0       577       50.000000
5248  2016-10-04 07:59:00      237.0      1200       51.975000
6560  2016-10-04 07:59:00      249.0       485       57.109021
2624  2016-10-04 07:59:00      117.0       470       59.598382
7872  2016-10-04 07:59:00      178.0       690       62.178092
...                   ...        ...       ...             ...
2623  2016-12-19 16:30:00      387.0       387    65316.002622
1311  2016-12-19 16:30:00      193.0       577    65319.347510
10495 2016-12-19 16:30:00     1345.0      2009    65326.042383
3935  2016-12-19 16:30:00      373.0       470    65333.978553
12207                 NaT        NaN      3883             NaN

[12208 rows x 4 columns]

***MODEL 2 :-***  Demand-Based Price Function

In [14]:
# Step 1: Encode categorical values
traffic_map = {'low': 1, 'medium': 2, 'high': 3}
vehicle_type_weight = {'car': 1.0, 'bike': 0.8, 'bus': 1.2, 'truck': 1.5}

df['TrafficLevel'] = df['TrafficConditionNearby'].map(traffic_map)
df['VehicleTypeWeight'] = df['VehicleType'].map(vehicle_type_weight)

# Step 2: Calculate Occupancy Rate
df['OccupancyRate'] = df['Occupancy'] / df['Capacity']

# Step 3: Demand function parameters
alpha = 1.2
beta = 0.8
gamma = 0.5
delta = 1.0
epsilon = 0.6

# Step 4: Calculate Demand
df['Demand'] = (
    alpha * df['OccupancyRate'] +
    beta * df['QueueLength'] -
    gamma * df['TrafficLevel'] +
    delta * df['IsSpecialDay'] +
    epsilon * df['VehicleTypeWeight']
)

# Step 5: Normalize Demand
df['Norm6alizedDemand'] = (df['Demand'] - df['Demand'].min()) / (df['Demand'].max() - df['Demand'].min())

# Step 6: Price Calculation
BasePrice = 100
lambda_coeff = 0.5

df['DynamicPrice'] = BasePrice * (1 + lambda_coeff * df['NormalizedDemand'])

# Step 7: Apply bounds
df['FinalPrice'] = df['DynamicPrice'].clip(lower=BasePrice * 0.5, upper=BasePrice * 2.0)

# Step 8: Bokeh Interactive Plot
source = ColumnDataSource(df)

p = figure(title="Demand-Based Dynamic Pricing", x_axis_label="Time ID", y_axis_label="Price", width=800, height=400)
p.line(x='ID', y='FinalPrice', source=source, line_width=2, color="navy", legend_label="Final Price")
p.circle(x='ID', y='FinalPrice', source=source, size=8, fill_color="orange", legend_label="Data Points")

hover = HoverTool(
    tooltips=[
        ("ID", "@ID"),
        ("Occupancy", "@Occupancy"),
        ("Queue Length", "@QueueLength"),
        ("Traffic", "@TrafficLevel"),
        ("Price", "@FinalPrice{0.00}"),
        ("Time", "@LastUpdatedTime")
    ]
)

p.add_tools(hover)
p.legend.location = "top_left"
p.grid.grid_line_alpha = 0.3

# Step 9: Show plot
show(p)


***MODEL 3 :-*** Competitive Pricing Model

In [13]:
# Step 1: Define a list of nearby competitor parking lots with their name, location (latitude & longitude)
competitors = [
    {"name": "CompA", "lat": 26.145, "lon": 91.737, "price": 50},
    {"name": "CompB", "lat": 26.144, "lon": 91.734, "price": 60},
    {"name": "CompC", "lat": 26.143, "lon": 91.735, "price": 70},
]

# Step 2: Define pricing function with competition logic
def competitive_price(row, base_price=50, alpha=10):
    your_loc = (row['Latitude'], row['Longitude'])
    occupancy_ratio = row['Occupancy'] / row['Capacity']
    your_price = base_price + alpha * occupancy_ratio

    # Compute nearby competitor influence
    nearby_prices = []
    for comp in competitors:
        comp_loc = (comp['lat'], comp['lon'])
        dist = geodesic(your_loc, comp_loc).meters
        if dist < 500:  # within 500m considered competition
            nearby_prices.append(comp['price'])

    avg_comp_price = np.mean(nearby_prices) if nearby_prices else your_price

    # Adjust price based on comparison
    if occupancy_ratio > 0.9 and your_price > avg_comp_price:
        your_price -= 5  # reduce to stay competitive
    elif avg_comp_price > your_price:
        your_price += 3  # increase to follow market

    return round(your_price, 2)

# Step 3: Apply pricing model
df['CompetitivePrice'] = df.apply(competitive_price, axis=1)

# Step 4: Plot with Bokeh
source = ColumnDataSource(df)

p = figure(title="Competitive Pricing Model Over Time", x_axis_type='datetime', width=800, height=400)
p.line(x='Datetime', y='CompetitivePrice', source=source, line_width=2, color="green", legend_label="Your Lot Price")
p.circle(x='Datetime', y='CompetitivePrice', source=source, size=8, color="green")

hover = HoverTool(tooltips=[
    ("Time", "@Datetime{%H:%M}"),
    ("Price", "@CompetitivePrice"),
    ("Occupancy", "@Occupancy"),
], formatters={'@Datetime': 'datetime'})

p.add_tools(hover)
p.legend.location = "top_left"
p.xaxis.axis_label = 'Time'
p.yaxis.axis_label = 'Price'
show(p)
